In [1]:
import pandas as pd
import sqlalchemy
from sshtunnel import SSHTunnelForwarder
from db_data import *
import plotly.express as px

### Pobranie danych

In [24]:
server = SSHTunnelForwarder(
    (sshhost, sshport),
    ssh_username=sshuser,
    ssh_password=sshpass,
    remote_bind_address=(sshbhost, sshbport)
    )
server.start()
local_port = str(server.local_bind_port)
engine = sqlalchemy.create_engine(f'{dbtype}://{dbuser}:{dbpass}@localhost:{local_port}/{dbname}')
hydro_stations = pd.read_sql(hstable, engine)
hydro_data = pd.read_sql(hdtable, engine)
weather_stations = pd.read_sql(wstable, engine)
weather_data = pd.read_sql(wdtable, engine)
server.stop()
print("dane pogodowe:", len(weather_data))
print("dane hydrologiczne:", len(hydro_data))

dane pogodowe: 24632
dane hydrologiczne: 219853


### Przygotowanie danych

In [25]:
hydro_stations.dropna(inplace=True)
hydro_stations.set_index("station_id", inplace=True)

# Resample data
hydro_data['station_id'] = hydro_data['station_id'].astype("category")
hydro_data = hydro_data.groupby(by="station_id").resample('3H', on="datetime").mean()
hydro_data.reset_index(inplace=True)

# Fill NaN
hydro_data["value"] = (hydro_data.ffill()["value"]+hydro_data.bfill()["value"])/2
hydro_data["value"] = hydro_data["value"].bfill().ffill()

### Odchylenie od średniej
# means = hydro_data.groupby("station_id").mean().reset_index()
# hydro_data = hydro_data.merge(means, how="left", on="station_id", suffixes = ['', '_mean'])
# hydro_data["deviation"] = hydro_data['value'] - hydro_data['value_mean']
# hydro_data.drop(columns=["value_mean","value"], inplace=True)
# # hydro_data["deviation"] = hydro_data["deviation"].transform(lambda x: x / abs(x).max())
# hydro_data["deviation"] = hydro_data["deviation"].transform(lambda x: ((x / abs(x).max())+1)*5).astype("int")
###

hydro_data.loc[hydro_data["station_id"] == hydro_data["station_id"].shift(1), "change"] = hydro_data["value"] - hydro_data["value"].shift(1)
hydro_data["change"].fillna(0, inplace = True)
hydro_data["change_percent"] = hydro_data["change"]/hydro_data["value"]


In [26]:
hydro_data = hydro_data.merge(hydro_stations, on="station_id")

hydro_data = hydro_data[hydro_data["river"].str.startswith("Wisła")]
hydro_data.sort_values("kilometer", inplace=True)

hydro_data

station_id            datetime       value    change  change_percent  \
0      149180080 2021-06-25 09:00:00  133.500000  0.000000        0.000000   
2915   150190140 2021-06-30 12:00:00   72.000000  0.000000        0.000000   
2916   150190140 2021-06-30 15:00:00   72.000000  0.000000        0.000000   
2917   150190140 2021-06-30 18:00:00   72.000000  0.000000        0.000000   
2918   150190140 2021-06-30 21:00:00   72.000000  0.000000        0.000000   
...          ...                 ...         ...       ...             ...   
3197   150190360 2021-07-01 12:00:00  171.333333  0.666667        0.003891   
3198   150190360 2021-07-01 15:00:00  175.000000  3.666667        0.020952   
3199   150190360 2021-07-01 18:00:00  171.000000 -4.000000       -0.023392   
3193   150190360 2021-07-01 00:00:00  170.000000  2.000000        0.011765   
3180   150190360 2021-06-29 09:00:00  171.333333  2.000000        0.011673   

                                           station_name  \
0     Drogomyśl                                     ...   
2915  Bieruń Nowy                                   ...   
2916  Bieruń Nowy                                   ...   
2917  Bieruń Nowy                                   ...   
2918  Bieruń Nowy                                   ...   
...                                                 ...   
3197  Gromiec                                       ...   
3198  Gromiec                                       ...   
3199  Gromiec                                       ...   
3193  Gromiec                                       ...   
3180  Gromiec                                       ...   

                                                  river   latitude  longitude  \
0     Wisła                                         ...  49.869171  18.749649   
2915  Wisła                                         ...  50.063909  19.192508   
2916  Wisła                                         ...  50.063909  19.192508   
2917  Wisła                                         ...  50.063909  19.192508   
2918  Wisła                                         ...  50.063909  19.192508   
...                                                 ...        ...        ...   
3197  Wisła                                         ...  50.056624  19.293914   
3198  Wisła                                         ...  50.056624  19.293914   
3199  Wisła                                         ...  50.056624  19.293914   
3193  Wisła                                         ...  50.056624  19.293914   
3180  Wisła                                         ...  50.056624  19.293914   

      kilometer  
0           0.0  
2915        0.0  
2916        0.0  
2917        0.0  
2918        0.0  
...         ...  
3197      904.0  
3198      904.0  
3199      904.0  
3193      904.0  
3180      904.0  

[3562 rows x 10 columns]

In [27]:
weather_data['station_id'] = weather_data['station_id'].astype("category")
weather_data = weather_data.groupby(by="station_id").resample('3H', on="datetime").mean()
weather_data.reset_index(inplace=True)
weather_data = weather_data.merge(weather_stations, on="station_id")

weather_data["value"] = (weather_data.ffill()["value"]+weather_data.bfill()["value"])/2
weather_data["value"] = weather_data["value"].bfill().ffill()

In [9]:
# weather_data.loc[weather_data["value"] == 0, "value"] = 1

In [20]:
# weather_data[weather_data["value"]>50]


In [28]:
weather_data

station_id   datetime  value  \
0          12001 2021-06-25    0.0   
1          12001 2021-06-26    0.0   
2          12001 2021-06-27    0.0   
3          12001 2021-06-28    0.0   
4          12001 2021-06-29    0.0   
...          ...        ...    ...   
1111       12695 2021-07-08    0.0   
1112       12695 2021-07-09    0.0   
1113       12695 2021-07-10    0.0   
1114       12695 2021-07-11    0.0   
1115       12695 2021-07-12    0.0   

                                           station_name   latitude  longitude  
0     Platforma                                     ...        NaN        NaN  
1     Platforma                                     ...        NaN        NaN  
2     Platforma                                     ...        NaN        NaN  
3     Platforma                                     ...        NaN        NaN  
4     Platforma                                     ...        NaN        NaN  
...                                                 ...        ...        ...  
1111  Przemyśl                                      ...  49.784197  22.775473  
1112  Przemyśl                                      ...  49.784197  22.775473  
1113  Przemyśl                                      ...  49.784197  22.775473  
1114  Przemyśl                                      ...  49.784197  22.775473  
1115  Przemyśl                                      ...  49.784197  22.775473  

[1116 rows x 6 columns]

### Wykresy

In [29]:
fig = px.scatter_mapbox(hydro_data, lat='latitude', lon='longitude',
                        hover_name='station_name', animation_frame=hydro_data.datetime.astype(str), 
                        color="change_percent", range_color=[-0.05,0.05],
                       color_continuous_scale=[(0, "red"), (0.5, "yellow"), (1, "blue")])

fig.update_layout(mapbox_style='carto-positron',
                    margin={'r': 10, 't': 10, 'l': 10, 'b': 10})
fig.show()

In [15]:
fig = px.scatter_mapbox(weather_data, lat='latitude', lon='longitude',
                        hover_name='station_name', animation_frame=weather_data.datetime.astype(str),
                        color=weather_data.value.astype(int), range_color=[0,20],
                        color_continuous_scale=[(0, "white"), (1, "blue")] )

fig.update_layout(mapbox_style='carto-positron',
                    margin={'r': 10, 't': 10, 'l': 10, 'b': 10})
fig.show()

In [16]:
wisla = hydro_data[hydro_data["river"].str.startswith("Wisła")]
wisla.sort_values("kilometer", inplace=True)

In [18]:
px.line(data_frame=hydro_data, x='station_name', y='change', animation_frame=hydro_data.datetime.astype(str), range_y=[-20,20])

In [ ]:
wisla.so